### Ноутбук с подготовкой данных 

In [216]:
import json
import pandas as pd
import numpy as np

In [217]:
f = open('arxivData.json')
df = pd.read_json(f)

In [218]:
#df.head()

Данные загрузились нормально, теперь выберем нужные нам колонки.

In [219]:
data = df.drop(['author', 'day', 'id', 'link', 'month', 'year'], axis=1)

In [220]:
#data.head()

Теперь данные нужно привести к удобному виду:

In [221]:
data['summary'] = data['summary'].apply(lambda x : x.lower())
data['title'] = data['title'].apply(lambda x : x.lower())

In [222]:
def extract(term_line):
    line = eval(term_line)
    for elem in line:
        try:
            return elem['term'].split('.')[0]
        except Exception:
            pass

In [223]:
data['tag'] = data['tag'].apply(lambda x : extract(x))

In [224]:
data.head()

summary   tag  \
0  we propose an architecture for vqa which utili...    cs   
1  recent approaches based on artificial neural n...    cs   
2  we introduce the multiresolution recurrent neu...    cs   
3  multi-task learning is motivated by the observ...  stat   
4  we present milabot: a deep reinforcement learn...    cs   

                                               title  
0  dual recurrent attention units for visual ques...  
1  sequential short-text classification with recu...  
2  multiresolution recurrent neural networks: an ...  
3  learning what to share between loosely related...  
4              a deep reinforcement learning chatbot

In [225]:
from collections import Counter

In [226]:
Counter(data['tag'])

Counter({'cs': 34597,
         'stat': 4782,
         'astro-ph': 59,
         'q-bio': 320,
         'eess': 75,
         'cond-mat': 65,
         'math': 612,
         'physics': 216,
         'quant-ph': 66,
         'q-fin': 30,
         'gr-qc': 4,
         'nlin': 47,
         'cmp-lg': 110,
         'econ': 5,
         'hep-ex': 4,
         'hep-th': 1,
         'nucl-th': 1,
         'hep-ph': 2,
         'hep-lat': 2,
         'adap-org': 2})

Мы столкнулись с проблемой: классы сильно несбалансированы, на computer scince приходится более 85% от всех статей, половина от оставшихся значений приходится на statistics. Так что с большой долей вероятности, обученная модель будет возвращать один из этих классов. По-хорошему стоило бы уравновесить классы, но мы попробуем добавить статьи из архива в малочисленные категории, а из cs часть данных удалим, потому что перевес слишком большой.

In [227]:
import arxiv

In [228]:
additional_cat = [] 
additional_title = []
additional_summary = []
search = arxiv.Search(
  query = 'all',
  max_results = 7000,
  sort_by = arxiv.SortCriterion.SubmittedDate
)
for result in search.results():
    print(result.primary_category)
    if result.primary_category[:2] != 'cs':
        additional_cat.append(result.primary_category)
        additional_title.append(result.title)
        additional_summary.append(result.summary)

cs.CV
cs.LG
cs.RO
cs.LG
eess.SY
hep-th
math.DG
cs.LG
astro-ph.GA
cs.NI
cond-mat.soft
cs.LO
cs.LG
gr-qc
stat.ME
cs.CV
math.RT
cs.LG
cs.CV
hep-ex
cs.CV
stat.ML
astro-ph.CO
physics.optics
quant-ph
cs.CV
cs.LG
math.PR
cs.CV
astro-ph.SR
math.AG
math.MG
math.LO
hep-ph
math.KT
q-bio.QM
stat.ME
math.AP
cs.LG
cs.MA
cs.LG
cond-mat.mtrl-sci
cs.AR
math.CA
cs.CV
eess.IV
physics.atom-ph
math.AP
cs.IR
cond-mat.mtrl-sci
math.AP
cond-mat.mes-hall
math.DG
eess.AS
math.NA
cs.CR
math.PR
q-bio.QM
cs.CR
cs.IT
math.RT
math.RT
math.RT
cs.CV
math.RT
astro-ph.HE
math.DG
math.OC
math.RT
astro-ph.GA
physics.optics
stat.AP
cond-mat.supr-con
cs.CV
math.NA
cond-mat.mes-hall
quant-ph
cs.LG
cs.LG
hep-ph
astro-ph.HE
math.GR
math.SG
econ.EM
cs.LG
cs.CL
cs.LG
math.NT
cs.CV
cs.SE
cs.AI
math.AG
physics.comp-ph
astro-ph.HE
cond-mat.str-el
cs.LG
physics.ao-ph
quant-ph
astro-ph.SR
cs.CV
cs.CV
cs.NI
cs.CV
cs.SI
stat.ML
cs.DS
cs.CV
eess.IV
cs.CV
astro-ph.GA
cond-mat.mtrl-sci
cs.CV
stat.ML
cs.DS
cs.LG
physics.optics
hep-ex
math.

UnexpectedEmptyPageError: Page of results was unexpectedly empty (http://export.arxiv.org/api/query?search_query=all&id_list=&sortBy=submittedDate&sortOrder=descending&start=3200&max_results=100)

In [229]:
df_additional = pd.DataFrame(list(zip(additional_summary, additional_cat, additional_title)),
               columns =['summary', 'category', 'title'])      

In [230]:
df_additional

summary           category  \
0     This paper outlines a complete methodology for...            eess.SY   
1     We show that associativity of the tree-level O...             hep-th   
2     Let dimensions $d\ge 3$, and codimensions $c\g...            math.DG   
3     Carbon-enhanced metal-poor (CEMP) stars make-u...        astro-ph.GA   
4     This paper studies the features of a homopolym...      cond-mat.soft   
...                                                 ...                ...   
1958  Predicting structural and energetic properties...    physics.chem-ph   
1959  When normal metals (NMs) are attached to topol...  cond-mat.mes-hall   
1960  Nowcasting can play a key role in giving polic...            stat.ML   
1961  There is an increasing trend of research in me...            stat.ME   
1962  Cluster-robust inference is widely used in mod...            econ.EM   

                                                  title  
0     Modeling, robust control synthesis and worst-c...  
1      On Effective Field Theories with Celestial Duals  
2     Homologically area minimizing surfaces with no...  
3     Over 2.7 Million Carbon-Enhanced Metal-Poor st...  
4     End-pulled polymer translocation through a man...  
...                                                 ...  
1958  Transferring Chemical and Energetic Knowledge ...  
1959  Proximity-induced zero-energy states indisting...  
1960  Benchmarking Econometric and Machine Learning ...  
1961  Comparison of Effect Size Measures for Mediati...  
1962  Leverage, Influence, and the Jackknife in Clus...  

[1963 rows x 3 columns]

In [231]:
df_additional['summary'] = df_additional['summary'].apply(lambda x : x.lower())
df_additional['title'] = df_additional['title'].apply(lambda x : x.lower())

In [232]:
def extract_cat(term_line):
    try:
        return term_line.split('.')[0]
    except Exception:
        pass

In [233]:
df_additional['tag'] = df_additional['category'].apply(lambda x : extract_cat(x))

In [234]:
df_additional = df_additional.drop(['category'], axis=1)

In [235]:
Counter(df_additional['tag'])

Counter({'eess': 102,
         'hep-th': 66,
         'math': 573,
         'astro-ph': 292,
         'cond-mat': 181,
         'gr-qc': 73,
         'stat': 96,
         'hep-ex': 29,
         'physics': 197,
         'quant-ph': 139,
         'hep-ph': 84,
         'q-bio': 34,
         'econ': 33,
         'hep-lat': 7,
         'nlin': 8,
         'nucl-th': 11,
         'math-ph': 25,
         'nucl-ex': 7,
         'q-fin': 6})

In [236]:
df_additional.head()

summary  \
0  this paper outlines a complete methodology for...   
1  we show that associativity of the tree-level o...   
2  let dimensions $d\ge 3$, and codimensions $c\g...   
3  carbon-enhanced metal-poor (cemp) stars make-u...   
4  this paper studies the features of a homopolym...   

                                               title       tag  
0  modeling, robust control synthesis and worst-c...      eess  
1   on effective field theories with celestial duals    hep-th  
2  homologically area minimizing surfaces with no...      math  
3  over 2.7 million carbon-enhanced metal-poor st...  astro-ph  
4  end-pulled polymer translocation through a man...  cond-mat

In [237]:
new_additional = df_additional[['summary','tag','title']].copy()

In [238]:
new_additional.head()

summary       tag  \
0  this paper outlines a complete methodology for...      eess   
1  we show that associativity of the tree-level o...    hep-th   
2  let dimensions $d\ge 3$, and codimensions $c\g...      math   
3  carbon-enhanced metal-poor (cemp) stars make-u...  astro-ph   
4  this paper studies the features of a homopolym...  cond-mat   

                                               title  
0  modeling, robust control synthesis and worst-c...  
1   on effective field theories with celestial duals  
2  homologically area minimizing surfaces with no...  
3  over 2.7 million carbon-enhanced metal-poor st...  
4  end-pulled polymer translocation through a man...

In [239]:
frames = [data, new_additional]

In [240]:
merged_data = pd.concat(frames)

In [241]:
merged_data.head()

summary   tag  \
0  we propose an architecture for vqa which utili...    cs   
1  recent approaches based on artificial neural n...    cs   
2  we introduce the multiresolution recurrent neu...    cs   
3  multi-task learning is motivated by the observ...  stat   
4  we present milabot: a deep reinforcement learn...    cs   

                                               title  
0  dual recurrent attention units for visual ques...  
1  sequential short-text classification with recu...  
2  multiresolution recurrent neural networks: an ...  
3  learning what to share between loosely related...  
4              a deep reinforcement learning chatbot

In [242]:
Counter(merged_data['tag'])

Counter({'cs': 34597,
         'stat': 4878,
         'astro-ph': 351,
         'q-bio': 354,
         'eess': 177,
         'cond-mat': 246,
         'math': 1185,
         'physics': 413,
         'quant-ph': 205,
         'q-fin': 36,
         'gr-qc': 77,
         'nlin': 55,
         'cmp-lg': 110,
         'econ': 38,
         'hep-ex': 33,
         'hep-th': 67,
         'nucl-th': 12,
         'hep-ph': 86,
         'hep-lat': 9,
         'adap-org': 2,
         'math-ph': 25,
         'nucl-ex': 7})

Как видим ситуация стала лучше. Теперь данные можно почистить от лишнего

In [243]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /Users/seal/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [244]:
trash = nltk.corpus.stopwords.words('english')

In [245]:
def clean_data(line):
    output= [i for i in line.split() if i not in trash]
    return ' '.join(output)

In [246]:
merged_data['summary'] = merged_data['summary'].apply(lambda x : clean_data(x))
merged_data['title'] = merged_data['title'].apply(lambda x : clean_data(x))

In [247]:
merged_data.head()

summary   tag  \
0  propose architecture vqa utilizes recurrent la...    cs   
1  recent approaches based artificial neural netw...    cs   
2  introduce multiresolution recurrent neural net...    cs   
3  multi-task learning motivated observation huma...  stat   
4  present milabot: deep reinforcement learning c...    cs   

                                               title  
0  dual recurrent attention units visual question...  
1  sequential short-text classification recurrent...  
2  multiresolution recurrent neural networks: app...  
3               learning share loosely related tasks  
4                deep reinforcement learning chatbot

Закодируем таргет для более удобной работы

In [248]:
from sklearn.preprocessing import LabelEncoder

In [249]:
merged_data.tag.value_counts()

cs          34597
stat         4878
math         1185
physics       413
q-bio         354
astro-ph      351
cond-mat      246
quant-ph      205
eess          177
cmp-lg        110
hep-ph         86
gr-qc          77
hep-th         67
nlin           55
econ           38
q-fin          36
hep-ex         33
math-ph        25
nucl-th        12
hep-lat         9
nucl-ex         7
adap-org        2
Name: tag, dtype: int64

In [250]:
merged_data = merged_data.drop(merged_data[merged_data.tag == 'adap-org'].index)
merged_data = merged_data.drop(merged_data[merged_data.tag == 'nucl-ex'].index)
merged_data = merged_data.drop(merged_data[merged_data.tag == 'hep-lat'].index)

In [251]:
label_encoder = LabelEncoder()
merged_data['tags'] = label_encoder.fit_transform(merged_data['tag'])

Поскольку модель должна обрабатывать запросы как содержащие summary и title сразу, так и содержащие только одно заполненнное поле, сольём эти данные в одну колонку

In [252]:
merged_data['full_info'] = merged_data['title'] + '. ' + merged_data['summary']

Избавимся от лишнего

In [253]:
merged_data = merged_data.drop(['summary', 'tag', 'title'], axis=1)

In [254]:
merged_data.head()

tags                                          full_info
0     3  dual recurrent attention units visual question...
1     3  sequential short-text classification recurrent...
2     3  multiresolution recurrent neural networks: app...
3    18  learning share loosely related tasks. multi-ta...
4     3  deep reinforcement learning chatbot. present m...

In [255]:
from imblearn.datasets import make_imbalance

In [256]:
X = merged_data.drop(['tags'], axis=1)
y = merged_data['tags']

In [257]:
Counter(y)

Counter({3: 34584,
         18: 4877,
         0: 351,
         15: 354,
         5: 177,
         2: 246,
         10: 1185,
         14: 413,
         17: 205,
         16: 36,
         6: 77,
         12: 55,
         1: 110,
         4: 38,
         7: 33,
         9: 67,
         13: 12,
         8: 86,
         11: 25})

Теперь выбросим часть данных cs и stats

In [258]:
X_balanced, y_balanced = make_imbalance(X, y,
                              sampling_strategy={0: 351,
                                                 1: 110,
                                                 2: 246,
                                                 3: 7279,
                                                 4: 38,
                                                 5: 177,
                                                 6: 77,
                                                 7: 33,
                                                 8: 86,
                                                 9: 67,
                                                 10: 1185,
                                                 11: 25, 
                                                 12: 55, 
                                                 13: 12, 
                                                 14: 413, 
                                                 15: 354,
                                                 16: 36, 
                                                 17: 205,  
                                                 18: 3231
                                                },
                              random_state=123)

In [259]:
Counter(y_balanced)

Counter({0: 351,
         1: 110,
         2: 246,
         3: 7279,
         4: 38,
         5: 177,
         6: 77,
         7: 33,
         8: 86,
         9: 67,
         10: 1185,
         11: 25,
         12: 55,
         13: 12,
         14: 413,
         15: 354,
         16: 36,
         17: 205,
         18: 3231})

In [260]:
X_balanced['tags'] = y_balanced

In [261]:
#X_balanced.head()

In [268]:
from sklearn.model_selection import train_test_split
# возьмём маленький размер тестовой выборки, чтобы в train попало как можно больше классов
train, test = train_test_split(X_balanced, test_size=0.15, shuffle=True,random_state=123)

In [269]:
train.to_csv('data_train.csv', index=None)
test.to_csv('data_test.csv', index=None)

Будем считать, что данные подготовлены к тому, чтобы что-то на них обучить.

In [171]:
name_dict = {3: 'cs',
         18: 'stat',
         10: 'math',
         14: 'physics',
         15: 'q-bio',
         0: 'astro-ph',             
         2: 'cond-mat',
         17: 'quant-ph',            
         5: 'eess',       
         1: 'cmp-lg',
         8: 'hep-ph',             
         6: 'gr-qc',
         9: 'hep-th',             
         12: 'nlin',            
         4: 'econ'  
         16: 'q-fin',             
         7: 'hep-ex',            
         11: 'math-ph',
         13: 'nucl-th'}